# Generate mutations (in PDB files)

In [1]:
import os
import re
from openmm.app import PDBFile
import pdbfixer
import pandas as pd

Read mutations from external csv file at https://osf.io/download/8v7hz/

In [2]:
mutation_data = pd.read_csv("https://osf.io/download/8v7hz/")
mutation_data

MUTATION  min_improvement_by_simulation  Position
0     E282K                      -0.548820       282
1     L298F                      -0.479801       298
2     M351K                      -0.197845       351
3     E292V                      -0.129575       292
4     D325G                      -0.064600       325
..      ...                            ...       ...
83    E255K                       1.493937       255
84    G250E                       1.594206       250
85    N368S                       1.636198       368
86    G251D                       1.700431       251
87    E255V                       1.809373       255

[88 rows x 3 columns]

In [3]:
# Utility structures and functions  
# Create dictionary for AA code translation
aa_three_to_one_code = {
    "ALA": "A",
    "GLY": "G",
    "ILE": "I",
    "LEU": "L",
    "PRO": "P",
    "VAL": "V",
    "PHE": "F",
    "TRP": "W",
    "TYR": "Y",
    "ASP": "D",
    "GLU": "E",
    "ARG": "R",
    "HIS": "H",
    "LYS": "K",
    "SER": "S",
    "THR": "T",
    "CYS": "C",
    "MET": "M",
    "ASN": "N",
    "GLN": "Q"
}
aa_one_to_three_code = {value: key for key, value in aa_three_to_one_code.items()}

# Utility functions/callables
def parse_mutation_spec(mutation_spec: str):
    """
    Parse a mutation specification string into its components: initial residue,
    residue number, and final residue.

    The input is expected to follow the format:
    "<initial_residue><residue_number><final_residue>", where both residues
    can be one- or three-letter uppercase or lowercase codes. The function
    automatically capitalizes the input before parsing.

    Examples of valid formats:
    - "Y2A"
    - "tyr23ala"
    - "Ace123NME"

    Parameters
    ----------
    mutation_spec : str
        A string representing a mutation (e.g., "Y2A", "TYR23ALA", "ace123nme").

    Returns
    -------
    tuple of str
        A tuple (initial_residue, residue_number, final_residue), where:
            - initial_residue is a 1–3 character uppercase string,
            - residue_number is a string of digits,
            - final_residue is a 1–3 character uppercase string.

    Raises
    ------
    ValueError
        If the mutation_spec does not match the expected pattern.
    """
    mutation_string = mutation_spec.upper()
    pattern = r'([A-Z]{1,3})(\d+)([A-Z]{1,3})'
    match = re.search(pattern, mutation_string)
    if match:
        initial_aa, res_number, final_aa = match.groups()
        return initial_aa, res_number, final_aa

    raise ValueError(f"Invalid mutation specification: {mutation_spec}")

In [4]:
input_pdb = "structures/abl1_structure.pdb"
for mutation_spec in mutation_data["MUTATION"]:
    # initiate pdb_fixer each time!
    pdb_fixer = pdbfixer.PDBFixer(filename=input_pdb)
    pdb_fixer.findMissingResidues()
    omm_top = pdb_fixer.topology
    chain_id = "A"  # TODO: A way to get this information from the "mutation_spec"?
    # Get mutation 
    initial_aa, res_num, final_aa = parse_mutation_spec(mutation_spec)
    mutation_str = "-".join([aa_one_to_three_code[initial_aa], res_num, aa_one_to_three_code[final_aa]])
    # Apply mutation
    pdb_fixer.applyMutations(mutations=[mutation_str], chain_id=chain_id)
    pdb_fixer.findMissingResidues()
    pdb_fixer.findMissingAtoms()
    pdb_fixer.addMissingAtoms()
    pdb_fixer.addMissingHydrogens()
    omm_topology = pdb_fixer.topology
    omm_positions = pdb_fixer.positions
    mutant_out_dir = "./mutant_structures"
    os.makedirs(mutant_out_dir, exist_ok=True)
    with open(f"{mutant_out_dir}/abl1_mut_{mutation_str}.pdb", "w") as out_file:
        PDBFile.writeFile(omm_topology, omm_positions, out_file)

FileNotFoundError: [Errno 2] No such file or directory: 'structures/abl1_structure.pdb'

# Generate mappings

In [7]:
from kartograf import KartografAtomMapper
from gufe import ProteinComponent

LICENSE: Could not open license file "oe_license.txt" in local directory
LICENSE: N.B. OE_LICENSE environment variable is not set
LICENSE: N.B. OE_DIR environment variable is not set
LICENSE: No product keys!
LICENSE: No product keys!
LICENSE: No product keys!
LICENSE: No product keys!
Error: 
  × could not find pixi.toml or pyproject.toml at directory /home/ijpulidos/
  │ workdir/repos/pale/playground/protein-mutation/ABL_dasatinib

/home/ijpulidos/miniforge3/envs/pale-dev/lib/python3.12/site-packages/openff/utilities/provenance.py:72: CondaExecutableNotFoundWarning: Something went wrong parsing the output of `conda list` or similar. Unable to determine AmberTools version, returning None.
  warnings.warn(
Error: 
  × could not find pixi.toml or pyproject.toml at directory /home/ijpulidos/
  │ workdir/repos/pale/playground/protein-mutation/ABL_dasatinib

/home/ijpulidos/miniforge3/envs/pale-dev/lib/python3.12/site-packages/openff/utilities/provenance.py:72: CondaExecutableNotFoundWarni

In [15]:
# Generating mappings for all the relevant mutations
reference_component = ProteinComponent.from_pdb_file("structures/abl1_structure.pdb")
atom_mapper = KartografAtomMapper()
#for mutation_string in mutation_data["Mutation"]:
for index, row in mutation_data.iterrows():
    mutation_string = row["MUTATION"]
    initial_aa_one_letter, mut_position, final_aa_one_letter = parse_mutation_spec(mutation_string)
    initial_aa_three_letter = aa_one_to_three_code[initial_aa_one_letter]
    final_aa_three_letter = aa_one_to_three_code[final_aa_one_letter]
    print(f"Generating {initial_aa_three_letter}{mut_position}{final_aa_three_letter} mutation mapping.")
    # Read mutant pdb component
    mutant_comp = ProteinComponent.from_pdb_file(f"mutant_structures/abl1_mut_{initial_aa_three_letter}-{mut_position}-{final_aa_three_letter}.pdb")
    # Generate mappings
    mapping = next(atom_mapper.suggest_mappings(reference_component, mutant_comp))
    #mutation_data.at[index, "atom_mapping"] = mapping
    # Serializing mappings
    os.makedirs("./mappings", exist_ok=True)
    with open(f"mappings/{initial_aa_three_letter}_{mut_position}_{final_aa_three_letter}.json", "w") as out_file:
        mapping.to_json(out_file)

Generating GLU282LYS mutation mapping.
Generating LEU298PHE mutation mapping.
Generating MET351LYS mutation mapping.
Generating GLU292VAL mutation mapping.
Generating ASP325GLY mutation mapping.
Generating ASP444TYR mutation mapping.
Generating VAL338PHE mutation mapping.
Generating LYS378ARG mutation mapping.
Generating GLY251GLU mutation mapping.
Generating GLN252MET mutation mapping.
Generating TYR253HIS mutation mapping.
Generating GLU494GLY mutation mapping.
Generating GLU279TYR mutation mapping.
Generating THR277ALA mutation mapping.
Generating SER438CYS mutation mapping.
Generating ALA433THR mutation mapping.
Generating TYR320CYS mutation mapping.
Generating GLU459GLY mutation mapping.
Generating GLU453LEU mutation mapping.
Generating GLU282GLY mutation mapping.
Generating MET343THR mutation mapping.
Generating PHE486SER mutation mapping.
Generating GLU450ALA mutation mapping.
Generating PHE311LEU mutation mapping.
Generating ASP276ALA mutation mapping.
Generating LYS419GLU muta

In [7]:
len(mapping.componentA_to_componentB)

4310

In [8]:
list(mapping.componentB_unique)

[367, 368, 369, 372]

In [9]:
reference_component.to_openmm_topology()

<Topology; 1 chains, 268 residues, 4313 atoms, 4369 bonds>

## Generate protocol DAGs

In [11]:
from gufe import ChemicalSystem, ProteinComponent, SolventComponent, SmallMoleculeComponent, LigandAtomMapping
from feflow.protocols import NonEquilibriumCyclingProtocol

In [12]:
# Specify settings for the protocol
settings = NonEquilibriumCyclingProtocol.default_settings()
settings.integrator_settings.equilibrium_steps = 375000  # Short for debugging
settings.integrator_settings.nonequilibrium_steps = 375000
settings.num_cycles = 100
settings.alchemical_settings.explicit_charge_correction = True
# Better charges with OE
settings.partial_charge_settings.partial_charge_method = "am1bccelf10"
settings.partial_charge_settings.off_toolkit_backend = "openeye"

In [13]:
settings

{'alchemical_settings': {'endstate_dispersion_correction': False,
                         'explicit_charge_correction': True,
                         'explicit_charge_correction_cutoff': <Quantity(0.8, 'nanometer')>,
                         'softcore_LJ': 'gapsys',
                         'softcore_alpha': 0.85,
                         'turn_off_core_unique_exceptions': False,
                         'use_dispersion_correction': False},
 'atom_selection_expression': 'not water',
 'engine_settings': {'compute_platform': None, 'gpu_device_index': None},
 'forcefield_cache': 'db.json',
 'forcefield_settings': {'constraints': 'hbonds',
                         'forcefields': ['amber/ff14SB.xml',
                                         'amber/tip3p_standard.xml',
                                         'amber/tip3p_HFE_multivalent.xml',
                                         'amber/phosaa10.xml'],
                         'hydrogen_mass': 3.0,
                         'nonbonded_c

In [16]:
# Create systems and protocol dags
initial_protein_comp = ProteinComponent.from_pdb_file("structures/abl1_structure.pdb")
ligand_comp = SmallMoleculeComponent.from_sdf_file("structures/kinoml_OEKLIFSKinaseHybridDockingFeaturizer_ABL1_2hyy_chainC_altloc-_imatinib_ligand.sdf")
solvent_comp = SolventComponent()
protocol = NonEquilibriumCyclingProtocol(settings=settings)
for mutation_string in mutation_data["MUTATION"]:
    initial_aa_one_letter, mut_position, final_aa_one_letter = parse_mutation_spec(mutation_string)
    initial_aa_three_letter = aa_one_to_three_code[initial_aa_one_letter]
    final_aa_three_letter = aa_one_to_three_code[final_aa_one_letter]
    final_protein_comp = ProteinComponent.from_pdb_file(f"mutant_structures/abl1_mut_{initial_aa_three_letter}-{mut_position}-{final_aa_three_letter}.pdb")
    # initial_state = ChemicalSystem(components={"protein": initial_protein_comp, "imatinib": ligand_comp, "solvent": solvent_comp})  # complex
    initial_state = ChemicalSystem(components={"protein": initial_protein_comp, "solvent": solvent_comp})  # apo
    # end_state = ChemicalSystem(components={"protein": final_protein_comp, "imatinib": ligand_comp, "solvent": solvent_comp})  # complex
    end_state = ChemicalSystem(components={"protein": final_protein_comp, "solvent": solvent_comp})  # apo
    mapping = LigandAtomMapping.from_json(f"mappings/{initial_aa_three_letter}_{mut_position}_{final_aa_three_letter}.json")
    dag_name = f"NEqCycDAG_{initial_aa_three_letter}-{mut_position}-{final_aa_three_letter}"
    protocol_dag = protocol.create(stateA=initial_state, stateB=end_state, mapping=mapping, 
                                   name=dag_name)
    protocol_dag_outdir = "./protocol_dags_apo"
    os.makedirs(protocol_dag_outdir, exist_ok=True)
    protocol_dag.to_json(f"{protocol_dag_outdir}/{dag_name}.json")

## Execute DAG/simulation
Only do this for testing. Do it in a batch job in HPC for production.

In [1]:
import pathlib
from gufe.protocols import execute_DAG

In [8]:
protocol_dag_deserialized = NonEquilibriumCyclingProtocol.from_json("NEqCycDAG_GLU-255-VAL_short_example.json")
results_path = pathlib.Path("./results_capped")
os.makedirs(results_path, exist_ok=True)
protocol_result_dag = execute_DAG(protocol_dag_deserialized, keep_shared=True, shared_basedir=results_path, scratch_basedir=results_path)

A charge difference of -1 is observed between the end states. This will be addressed by transforming a water into a Na+ ion
/home/ijpulidos/miniforge3/envs/pale-dev/lib/python3.12/site-packages/openfe/protocols/openmm_rfe/equil_rfe_methods.py:164: UserWarning: A charge difference of -1 is observed between the end states. This will be addressed by transforming a water into a Na+ ion
  warnings.warn(wmsg)


In [9]:
cycle_result = protocol_result_dag.protocol_unit_results[1]

In [10]:
cycle_result.end_time - cycle_result.start_time

datetime.timedelta(seconds=42, microseconds=285364)

## Read HTF -- check everything looks fine (DEBUGGING)

In [11]:
import numpy as np

In [12]:
htf_np = np.load("results_capped/shared_SetupUnit-31206a89bf834f31839ea1fefd496679_attempt_0/hybrid_topology_factory.pickle", allow_pickle=True)

In [13]:
htf_np._old_topology

<Topology; 4 chains, 13888 residues, 45088 atoms, 31529 bonds>

In [14]:
import mdtraj

In [15]:
# Read topology and positions
initial_top = htf_np._old_topology
initial_positions = htf_np.old_positions(htf_np.hybrid_positions)
final_top = htf_np._new_topology
final_positions = htf_np.new_positions(htf_np.hybrid_positions)
# Write to PDB
initial_pdb_file = "initial_topology.pdb"
final_pdb_file = "final_topology.pdb"
with open(initial_pdb_file, "w") as out_file:
    PDBFile.writeFile(initial_top, initial_positions, out_file)
with open(final_pdb_file, "w") as out_file:
    PDBFile.writeFile(final_top, final_positions, out_file)

In [51]:
initial_positions

Quantity(value=array([[ 7.4753    ,  7.2913    ,  0.9997    ],
       [ 7.4912    ,  7.3401    ,  1.1092    ],
       [ 7.5658    ,  7.3309    ,  0.8855    ],
       ...,
       [ 7.64180175,  2.87256175,  4.16710175],
       [ 6.76800175,  9.98596175,  1.44330175],
       [ 1.75260175,  3.44396175, -0.29589825]]), unit=nanometer)

In [55]:
np.shape(initial_positions)

(57743, 3)

In [56]:
np.shape(final_positions)

(57741, 3)

In [31]:
omm_top = htf_np._old_topology

In [33]:
initial_atoms = list(omm_top.atoms())

In [27]:
md_top = mdtraj.Topology.from_openmm(htf_np._old_topology)
md_traj = mdtraj.Trajectory(initial_positions, md_top)

In [28]:
import nglview

ModuleNotFoundError: No module named 'nglview'

In [29]:
htf_np._new_topology

<Topology; 5 chains, 18125 residues, 57741 atoms, 39944 bonds>

In [36]:
for initial_idx, final_idx in htf_np.old_to_hybrid_atom_map.items():
    if initial_idx == final_idx:
        print(f"Mapping differences: {initial_idx} to {final_idx}")
        print(f"Atom is: {initial_atoms[initial_idx]}")

Mapping differences: 0 to 0
Atom is: <Atom 0 (C) of chain 0 residue 0 (ACE)>
Mapping differences: 1 to 1
Atom is: <Atom 1 (O) of chain 0 residue 0 (ACE)>
Mapping differences: 2 to 2
Atom is: <Atom 2 (CH3) of chain 0 residue 0 (ACE)>
Mapping differences: 3 to 3
Atom is: <Atom 3 (H1) of chain 0 residue 0 (ACE)>
Mapping differences: 4 to 4
Atom is: <Atom 4 (H2) of chain 0 residue 0 (ACE)>
Mapping differences: 5 to 5
Atom is: <Atom 5 (H3) of chain 0 residue 0 (ACE)>
Mapping differences: 6 to 6
Atom is: <Atom 6 (N) of chain 0 residue 1 (ASP)>
Mapping differences: 7 to 7
Atom is: <Atom 7 (CA) of chain 0 residue 1 (ASP)>
Mapping differences: 8 to 8
Atom is: <Atom 8 (C) of chain 0 residue 1 (ASP)>
Mapping differences: 9 to 9
Atom is: <Atom 9 (O) of chain 0 residue 1 (ASP)>
Mapping differences: 10 to 10
Atom is: <Atom 10 (CB) of chain 0 residue 1 (ASP)>
Mapping differences: 11 to 11
Atom is: <Atom 11 (CG) of chain 0 residue 1 (ASP)>
Mapping differences: 12 to 12
Atom is: <Atom 12 (OD1) of chain

KeyboardInterrupt: 

In [35]:
htf_np.old_to_hybrid_atom_map

{0: 0,
 1: 1,
 2: 2,
 3: 3,
 4: 4,
 5: 5,
 6: 6,
 7: 7,
 8: 8,
 9: 9,
 10: 10,
 11: 11,
 12: 12,
 13: 13,
 14: 14,
 15: 15,
 16: 16,
 17: 17,
 18: 18,
 19: 19,
 20: 20,
 21: 21,
 22: 22,
 23: 23,
 24: 24,
 25: 25,
 26: 26,
 27: 27,
 28: 28,
 29: 29,
 30: 30,
 31: 31,
 32: 32,
 33: 33,
 34: 34,
 35: 35,
 36: 36,
 37: 37,
 38: 38,
 39: 39,
 40: 40,
 41: 41,
 42: 42,
 43: 43,
 44: 44,
 45: 45,
 46: 46,
 47: 47,
 48: 48,
 49: 49,
 50: 50,
 51: 51,
 52: 52,
 53: 53,
 54: 54,
 55: 55,
 56: 56,
 57: 57,
 58: 58,
 59: 59,
 60: 60,
 61: 61,
 62: 62,
 63: 63,
 64: 64,
 65: 65,
 66: 66,
 67: 67,
 68: 68,
 69: 69,
 70: 70,
 71: 71,
 72: 72,
 73: 73,
 74: 74,
 75: 75,
 76: 76,
 77: 77,
 78: 78,
 79: 79,
 80: 80,
 81: 81,
 82: 82,
 83: 83,
 84: 84,
 85: 85,
 86: 86,
 87: 87,
 88: 88,
 89: 89,
 90: 90,
 91: 91,
 92: 92,
 93: 93,
 94: 94,
 95: 95,
 96: 96,
 97: 97,
 98: 98,
 99: 99,
 100: 100,
 101: 101,
 102: 102,
 103: 103,
 104: 104,
 105: 105,
 106: 106,
 107: 107,
 108: 108,
 109: 109,
 110: 110,

In [37]:
from openmm.app import PDBFile

In [44]:
omm_top.getPeriodicBoxVectors()

Quantity(value=(Vec3(x=8.469396508789433, y=0, z=0), Vec3(x=0, y=8.469396508789433, z=0), Vec3(x=0, y=0, z=8.469396508789433)), unit=nanometer)

In [46]:
hybrid_top.to_openmm()

<Topology; 4 chains, 18125 residues, 57744 atoms, 39947 bonds>

In [47]:
htf_pdb_file = "./hybrid_topology.pdb"
hybrid_top = htf_np.hybrid_topology
hybrid_pos = htf_np.hybrid_positions
with open(htf_pdb_file, "w") as out_file:
    PDBFile.writeFile(hybrid_top.to_openmm(), hybrid_pos, out_file)

In [40]:
PDBFile.writeFile?

Signature:
PDBFile.writeFile(
    topology,
    positions,
    file=<ipykernel.iostream.OutStream object at 0x7c544ebf0c10>,
    keepIds=False,
    extraParticleIdentifier='EP',
)
Docstring:
Write a PDB file containing a single model.

Parameters
----------
topology : Topology
    The Topology defining the model to write
positions : list
    The list of atomic positions to write
file : string or file
    the name of the file to write.  Alternatively you can pass an open file object.
keepIds : bool=False
    If True, keep the residue and chain IDs specified in the Topology
    rather than generating new ones.  Warning: It is up to the caller to
    make sure these are valid IDs that satisfy the requirements of the
    PDB format.  Otherwise, the output file will be invalid.
extraParticleIdentifier : string='EP'
    String to write in the element column of the ATOM records for atoms whose element is None (extra particles)
File:      ~/miniforge3/envs/pale-dev/lib/python3.12/site-packages